---
draft: true 
date: 2025-01-08
description: "Calculating adjusted xG coefficients"
slug: adjusted-xg
---

# **Calculating score- and venue-adjusted xG coefficients**

---

## **Intro**

Intro language here

---

## **Housekeeping**

### Import dependencies

Import the dependencies we'll need to simulate today's games

In [1]:
import pandas as pd
import numpy as np
from scipy.stats import poisson

import chickenstats

from chickenstats.api import ChickenStats
from chickenstats.utilities import ChickenProgress
import chickenstats.utilities
from chickenstats.chicken_nhl import Season, Scraper
from chickenstats.chicken_nhl.scrape import Game

from rich.progress import track

from hockey_rink import NHLRink
import matplotlib.pyplot as plt
import matplotlib as mpl
from matplotlib.lines import Line2D
import matplotlib.patches as patches
import matplotlib.patheffects as mpe
import matplotlib.ticker as ticker
import seaborn as sns

from dotenv import load_dotenv
from pathlib import Path

import datetime as dt

import math

from typing import Optional

### Pandas options

Set different pandas options

In [2]:
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", 100)

### Load environment variables

Load environment variables to access the chickenstats API

In [3]:
env_file = Path("../../.env")
load_dotenv(env_file)

True

### Chickenstats matplotlib style

chickenstats.utilities includes a custom style package - this activates it

In [4]:
plt.style.use("chickenstats")

---

## **Load data**

In [5]:
concat_list = []

years = list(range(2023, 2009, -1))

for year in track(years):
    file_path = Path(
        f"../../../../chickenstats-api/data/chickenstats/raw/pbp/pbp_{year}.csv"
    )
    raw_df = pd.read_csv(file_path, low_memory=False)

    events = ["GOAL", "SHOT", "MISS", "BLOCK"]
    raw_df = raw_df.loc[raw_df.event.isin(events)]

    concat_list.append(raw_df)

Output()

In [6]:
shot_events_df = pd.concat(concat_list, ignore_index=True)

In [146]:
def prepare_shots_data(play_by_play: pd.DataFrame, strength_state: str) -> pd.DataFrame:
    """Docstring."""

    condition = play_by_play.strength_state == strength_state
    shots_data = play_by_play.loc[condition].reset_index(drop=True)

    shots_data["strength_state2"] = strength_state

    condition = shots_data.block == 1
    shots_data.event_team = np.where(
        condition, shots_data.opp_team, shots_data.event_team
    )

    shots_data.block = shots_data.block + shots_data.teammate_block

    conditions = [shots_data.home_score_diff < -3, shots_data.home_score_diff > 3]
    values = [-3, 3]
    shots_data.home_score_diff = np.select(
        conditions, values, shots_data.home_score_diff
    )

    shots_data.is_home = np.where(shots_data.event_team == shots_data.home_team, 1, 0)

    group_list = ["strength_state2", "home_score_diff", "is_home"]
    agg_stats = {x: "sum" for x in ["goal", "pred_goal", "shot", "miss", "block"]}
    shots_data = shots_data.groupby(group_list, as_index=False).agg(agg_stats)

    shots_data["fenwick"] = shots_data[["goal", "shot", "miss"]].sum(axis=1)
    shots_data["corsi"] = shots_data[["goal", "shot", "miss", "block"]].sum(axis=1)

    agg_stats = {}

    for stat in ["goal", "pred_goal", "shot", "miss", "block", "fenwick", "corsi"]:
        shots_data[f"home_{stat}"] = np.where(
            shots_data.is_home == 1, shots_data[stat], 0
        )
        shots_data[f"away_{stat}"] = np.where(
            shots_data.is_home == 0, shots_data[stat], 0
        )

        agg_stats.update({f"home_{stat}": "sum", f"away_{stat}": "sum"})

    shots_data = (
        shots_data.groupby(["strength_state2", "home_score_diff"], as_index=False)
        .agg(agg_stats)
        .rename(columns={"strength_state2": "strength_state"})
    )

    return shots_data

In [158]:
def calculate_weights(shots_data: pd.DataFrame) -> pd.DataFrame:
    """Docstring."""

    shots_data = shots_data.copy()

    strength_state = shots_data.strength_state.unique()[0]

    if strength_state in ["5v5", "4v4"]:
        weight_columns = ["fenwick", "corsi"]

        if strength_state == "5v5":
            weight_columns.insert(0, "shot")

        for weight_column in weight_columns:
            mean_values = shots_data[
                [f"home_{weight_column}", f"away_{weight_column}"]
            ].mean(axis=1)

            shots_data[f"home_{weight_column}_weight"] = (
                mean_values / shots_data[f"home_{weight_column}"]
            )
            shots_data[f"away_{weight_column}_weight"] = (
                mean_values / shots_data[f"away_{weight_column}"]
            )

    if strength_state in ["5v5", "4v4", "5v4", "5v3", "4v3", "1v0"]:
        if strength_state == "5v5":
            weight_columns = ["goal", "pred_goal"]

        if strength_state == "4v4":
            weight_columns = ["shot"]

        if strength_state in ["5v4", "5v3", "4v3"]:
            weight_columns = ["goal", "pred_goal", "shot", "fenwick", "corsi"]

        if strength_state == "1v0":
            weight_columns = ["goal"]

        weight_groups = ["trailing", "tied", "leading"]
        weight_group_conditions = [
            shots_data.home_score_diff < 0,
            shots_data.home_score_diff == 0,
            shots_data.home_score_diff > 0,
        ]

        shots_data["score_diff_group"] = np.select(
            weight_group_conditions, weight_groups, default=""
        )

        for weight_column in weight_columns:
            group_mean = (
                shots_data.groupby("score_diff_group")[
                    [f"home_{weight_column}", f"away_{weight_column}"]
                ]
                .transform("sum")[[f"home_{weight_column}", f"away_{weight_column}"]]
                .sum(axis=1)
            ) / 2

            group_home = shots_data.groupby("score_diff_group")[
                f"home_{weight_column}"
            ].transform("sum")

            group_away = shots_data.groupby("score_diff_group")[
                f"away_{weight_column}"
            ].transform("sum")

            shots_data[f"home_{weight_column}_weight"] = group_mean / group_home
            shots_data[f"away_{weight_column}_weight"] = group_mean / group_away

    if strength_state in ["4v4", "3v3"]:
        if strength_state == "4v4":
            weight_columns = ["goal", "pred_goal"]

        if strength_state == "3v3":
            weight_columns = ["goal", "pred_goal", "shot", "fenwick", "corsi"]

        for weight_column in weight_columns:
            group_mean = (
                shots_data.groupby("strength_state")[
                    [f"home_{weight_column}", f"away_{weight_column}"]
                ]
                .transform("sum")[[f"home_{weight_column}", f"away_{weight_column}"]]
                .sum(axis=1)
            ) / 2

            group_home = shots_data.groupby("strength_state")[
                f"home_{weight_column}"
            ].transform("sum")

            group_away = shots_data.groupby("strength_state")[
                f"away_{weight_column}"
            ].transform("sum")

            shots_data[f"home_{weight_column}_weight"] = group_mean / group_home
            shots_data[f"away_{weight_column}_weight"] = group_mean / group_away

    return shots_data

In [159]:
concat_list = []

strength_states = ["5v5", "4v4", "3v3", "5v4", "5v3", "4v3", "1v0"]

for strength_state in strength_states:
    shots_data = prepare_shots_data(
        play_by_play=shot_events_df, strength_state=strength_state
    )

    weights = calculate_weights(shots_data=shots_data)

    concat_list.append(weights)

In [160]:
test = pd.concat(concat_list, ignore_index=True)

In [168]:
columns = [
    "strength_state",
    "home_score_diff",
    "score_diff_group",
    "home_goal_weight",
    "away_goal_weight",
    "home_pred_goal_weight",
    "away_pred_goal_weight",
    "home_shot_weight",
    "away_shot_weight",
    "home_fenwick_weight",
    "away_fenwick_weight",
    "home_corsi_weight",
    "away_corsi_weight",
    "home_goal",
    "away_goal",
    "home_pred_goal",
    "away_pred_goal",
    "home_shot",
    "away_shot",
    "home_miss",
    "away_miss",
    "home_block",
    "away_block",
    "home_fenwick",
    "away_fenwick",
    "home_corsi",
    "away_corsi",
]

weights_dict = test[columns].to_dict(orient="records")

In [10]:
import pickle

In [11]:
with open("score_adjustments.pkl", "rb") as f:
    test_pickle = pickle.load(f)

In [5]:
season = Season(2024)
schedule = season.schedule("NSH")

game_ids = schedule.game_id.tolist()
game_id = game_ids[0]

Output()

In [6]:
game = Game(game_id)

In [7]:
play = [x for x in game.play_by_play if x["event"] == "GOAL"][0]

In [8]:
play

{'id': 20240200170324,
 'season': 20242025,
 'session': 'R',
 'game_id': 2024020017,
 'game_date': '2024-10-10',
 'event_idx': 324,
 'period': 2,
 'period_seconds': 125,
 'game_seconds': 1325,
 'strength_state': '5v5',
 'event_team': 'DAL',
 'opp_team': 'NSH',
 'event': 'GOAL',
 'description': 'DAL #24 HINTZ(1), WRIST , OFF. ZONE, 25 FT.ASSISTS: #11 STANKOVEN(1); #53 JOHNSTON(1) ',
 'zone': 'OFF',
 'coords_x': 69,
 'coords_y': 16,
 'danger': 1,
 'high_danger': 0,
 'player_1': 'ROOPE HINTZ',
 'player_1_eh_id': 'ROOPE.HINTZ',
 'player_1_eh_id_api': 'ROOPE.HINTZ',
 'player_1_api_id': 8478449,
 'player_1_position': 'C',
 'player_1_type': 'GOAL SCORER',
 'player_2': 'LOGAN STANKOVEN',
 'player_2_eh_id': 'LOGAN.STANKOVEN',
 'player_2_eh_id_api': 'LOGAN.STANKOVEN',
 'player_2_api_id': 8482702,
 'player_2_position': 'C',
 'player_2_type': 'PRIMARY ASSIST',
 'player_3': 'WYATT JOHNSTON',
 'player_3_eh_id': 'WYATT.JOHNSTON',
 'player_3_eh_id_api': 'WYATT.JOHNSTON',
 'player_3_api_id': 8482740,
 

In [8]:
weight_column = "home_block_weight"
weight_column = weight_column.replace("block", "corsi")

In [20]:
play["home_score_diff"]

0

In [9]:
weight_column

'home_corsi_weight'

In [9]:
score_adjustments = pd.DataFrame(test_pickle)

In [10]:
conditions = np.logical_and.reduce(
            [
                score_adjustments.strength_state == "1v0",
                score_adjustments["home_score_diff"] == -3,
            ]
        )

weight_column = "home_corsi_weight"

score_adjustments.loc[conditions][weight_column].iloc[0]

np.float64(nan)

In [17]:
def calculate_score_adjustment(play: dict, score_adjustments: pd.DataFrame) -> dict:
    """Calculates score adjustment for play."""

    if play["event"] in ["GOAL", "SHOT", "MISS", "BLOCK"]:
        if play["home_score_diff"] < -3:
            home_score_diff = -3
        elif play["home_score_diff"] > 3:
            home_score_diff = 3
        else:
            home_score_diff = play["home_score_diff"]

        if play["event"] == "BLOCK" and play["teammate_block"] == 0:
            event_team = play["opp_team"]
        else:
            event_team = play["event_team"]

        if event_team == play["home_team"]:
            is_home = 1
        else:
            is_home = 0

        adjusted_columns = [
            "goal",
            "pred_goal",
            "shot",
            "miss",
            "block",
            "fenwick",
            "corsi",
        ]

        for adjusted_column in adjusted_columns:
            if play["strength_state"] in ["4v5", "3v5", "3v4"]:

                if is_home == 1:
                    is_home = 0
                else:
                    is_home = 1
                strength_state = play["strength_state"][::-1]

            else:
                strength_state = play["strength_state"]

            if is_home == 1:
                weight_column = f"home_{adjusted_column}_weight"
            else:
                weight_column = f"away_{adjusted_column}_weight"

            if adjusted_column == "miss":
                weight_column = weight_column.replace("miss", "fenwick")

            if adjusted_column == "block":
                weight_column = weight_column.replace("block", "corsi")

            conditions = np.logical_and.reduce(
                [
                    score_adjustments.strength_state == strength_state,
                    score_adjustments["home_score_diff"] == home_score_diff,
                ]
            )

            if "E" not in strength_state:

                play[f"{adjusted_column}_adj"] = (
                    score_adjustments.loc[conditions][weight_column].iloc[0]
                    * play[adjusted_column]
                )

                if adjusted_column == "block" and play["block_adj"] == 0:
                    play["block_adj"] = (
                        play["teammate_block"] * score_adjustments.loc[conditions][weight_column].iloc[0]
                    )

            else:
                play[f"{adjusted_column}_adj"] = play[adjusted_column] * 1

                if adjusted_column == "block" and play["block_adj"] == 0:
                    play["block_adj"] = play["teammate_block"]

    return play

In [18]:
for play in game.play_by_play:

    display(calculate_score_adjustment(play, score_adjustments))

{'id': 20240200170001,
 'season': 20242025,
 'session': 'R',
 'game_id': 2024020017,
 'game_date': '2024-10-10',
 'event_idx': 1,
 'period': 1,
 'period_seconds': 0,
 'game_seconds': 0,
 'strength_state': 'EvE',
 'event_team': 'NSH',
 'opp_team': 'DAL',
 'event': 'PGSTR',
 'description': 'PRE-GAME START',
 'zone': None,
 'coords_x': None,
 'coords_y': None,
 'danger': None,
 'high_danger': None,
 'player_1': None,
 'player_1_eh_id': None,
 'player_1_eh_id_api': None,
 'player_1_api_id': None,
 'player_1_position': None,
 'player_1_type': None,
 'player_2': None,
 'player_2_eh_id': None,
 'player_2_eh_id_api': None,
 'player_2_api_id': None,
 'player_2_position': None,
 'player_2_type': None,
 'player_3': None,
 'player_3_eh_id': None,
 'player_3_eh_id_api': None,
 'player_3_api_id': None,
 'player_3_position': None,
 'player_3_type': None,
 'score_state': '0v0',
 'score_diff': 0,
 'forwards_percent': 0.0,
 'opp_forwards_percent': 0.0,
 'shot_type': None,
 'event_length': 0,
 'event_dis

{'id': 20240200170002,
 'season': 20242025,
 'session': 'R',
 'game_id': 2024020017,
 'game_date': '2024-10-10',
 'event_idx': 2,
 'period': 1,
 'period_seconds': 0,
 'game_seconds': 0,
 'strength_state': 'EvE',
 'event_team': 'NSH',
 'opp_team': 'DAL',
 'event': 'PGEND',
 'description': 'PRE-GAME END',
 'zone': None,
 'coords_x': None,
 'coords_y': None,
 'danger': None,
 'high_danger': None,
 'player_1': None,
 'player_1_eh_id': None,
 'player_1_eh_id_api': None,
 'player_1_api_id': None,
 'player_1_position': None,
 'player_1_type': None,
 'player_2': None,
 'player_2_eh_id': None,
 'player_2_eh_id_api': None,
 'player_2_api_id': None,
 'player_2_position': None,
 'player_2_type': None,
 'player_3': None,
 'player_3_eh_id': None,
 'player_3_eh_id_api': None,
 'player_3_api_id': None,
 'player_3_position': None,
 'player_3_type': None,
 'score_state': '0v0',
 'score_diff': 0,
 'forwards_percent': 0.0,
 'opp_forwards_percent': 0.0,
 'shot_type': None,
 'event_length': 0,
 'event_dista

{'id': 20240200170003,
 'season': 20242025,
 'session': 'R',
 'game_id': 2024020017,
 'game_date': '2024-10-10',
 'event_idx': 3,
 'period': 1,
 'period_seconds': 0,
 'game_seconds': 0,
 'strength_state': 'EvE',
 'event_team': 'NSH',
 'opp_team': 'DAL',
 'event': 'ANTHEM',
 'description': 'NATIONAL ANTHEM',
 'zone': None,
 'coords_x': None,
 'coords_y': None,
 'danger': None,
 'high_danger': None,
 'player_1': None,
 'player_1_eh_id': None,
 'player_1_eh_id_api': None,
 'player_1_api_id': None,
 'player_1_position': None,
 'player_1_type': None,
 'player_2': None,
 'player_2_eh_id': None,
 'player_2_eh_id_api': None,
 'player_2_api_id': None,
 'player_2_position': None,
 'player_2_type': None,
 'player_3': None,
 'player_3_eh_id': None,
 'player_3_eh_id_api': None,
 'player_3_api_id': None,
 'player_3_position': None,
 'player_3_type': None,
 'score_state': '0v0',
 'score_diff': 0,
 'forwards_percent': 0.0,
 'opp_forwards_percent': 0.0,
 'shot_type': None,
 'event_length': 0,
 'event_d

{'id': 20240200170004,
 'season': 20242025,
 'session': 'R',
 'game_id': 2024020017,
 'game_date': '2024-10-10',
 'event_idx': 4,
 'period': 1,
 'period_seconds': 0,
 'game_seconds': 0,
 'strength_state': 'EvE',
 'event_team': 'NSH',
 'opp_team': 'DAL',
 'event': 'PSTR',
 'description': 'PERIOD START- LOCAL TIME: 7:09 CDT',
 'zone': None,
 'coords_x': None,
 'coords_y': None,
 'danger': None,
 'high_danger': None,
 'player_1': None,
 'player_1_eh_id': None,
 'player_1_eh_id_api': None,
 'player_1_api_id': None,
 'player_1_position': None,
 'player_1_type': None,
 'player_2': None,
 'player_2_eh_id': None,
 'player_2_eh_id_api': None,
 'player_2_api_id': None,
 'player_2_position': None,
 'player_2_type': None,
 'player_3': None,
 'player_3_eh_id': None,
 'player_3_eh_id_api': None,
 'player_3_api_id': None,
 'player_3_position': None,
 'player_3_type': None,
 'score_state': '0v0',
 'score_diff': 0,
 'forwards_percent': 0.0,
 'opp_forwards_percent': 0.0,
 'shot_type': None,
 'event_leng

{'id': 20240200170005,
 'season': 20242025,
 'session': 'R',
 'game_id': 2024020017,
 'game_date': '2024-10-10',
 'event_idx': 5,
 'period': 1,
 'period_seconds': 0,
 'game_seconds': 0,
 'strength_state': '5vE',
 'event_team': 'NSH',
 'opp_team': 'DAL',
 'event': 'CHANGE',
 'description': 'PLAYERS ON: MARK JANKOWSKI, COLE SMITH, SCOTT WEDGEWOOD, MICHAEL MCCARRON, ROMAN JOSI, BRADY SKJEI',
 'zone': None,
 'coords_x': 0,
 'coords_y': 0,
 'danger': None,
 'high_danger': None,
 'player_1': None,
 'player_1_eh_id': None,
 'player_1_eh_id_api': None,
 'player_1_api_id': None,
 'player_1_position': None,
 'player_1_type': None,
 'player_2': None,
 'player_2_eh_id': None,
 'player_2_eh_id_api': None,
 'player_2_api_id': None,
 'player_2_position': None,
 'player_2_type': None,
 'player_3': None,
 'player_3_eh_id': None,
 'player_3_eh_id_api': None,
 'player_3_api_id': None,
 'player_3_position': None,
 'player_3_type': None,
 'score_state': '0v0',
 'score_diff': 0,
 'forwards_percent': 0.6,
 '

...

{'id': 20240200170809,
 'season': 20242025,
 'session': 'R',
 'game_id': 2024020017,
 'game_date': '2024-10-10',
 'event_idx': 809,
 'period': 3,
 'period_seconds': 1193,
 'game_seconds': 3593,
 'strength_state': 'Ev5',
 'event_team': 'NSH',
 'opp_team': 'DAL',
 'event': 'MISS',
 'description': 'NSH #91 STAMKOS, SNAP, WIDE RIGHT, OFF. ZONE, 46 FT. ',
 'zone': 'OFF',
 'coords_x': 52,
 'coords_y': 28,
 'danger': 0,
 'high_danger': 0,
 'player_1': 'STEVEN STAMKOS',
 'player_1_eh_id': 'STEVEN.STAMKOS',
 'player_1_eh_id_api': 'STEVEN.STAMKOS',
 'player_1_api_id': 8474564,
 'player_1_position': 'C',
 'player_1_type': 'SHOOTER',
 'player_2': None,
 'player_2_eh_id': None,
 'player_2_eh_id_api': None,
 'player_2_api_id': None,
 'player_2_position': None,
 'player_2_type': None,
 'player_3': None,
 'player_3_eh_id': None,
 'player_3_eh_id_api': None,
 'player_3_api_id': None,
 'player_3_position': None,
 'player_3_type': None,
 'score_state': '3v4',
 'score_diff': -1,
 'forwards_percent': 0.833

{'id': 20240200170810,
 'season': 20242025,
 'session': 'R',
 'game_id': 2024020017,
 'game_date': '2024-10-10',
 'event_idx': 810,
 'period': 3,
 'period_seconds': 1200,
 'game_seconds': 3600,
 'strength_state': 'Ev5',
 'event_team': 'NSH',
 'opp_team': 'DAL',
 'event': 'CHANGE',
 'description': "PLAYERS OFF: FILIP FORSBERG, COLTON SISSONS, ROMAN JOSI, JONATHAN MARCHESSAULT, RYAN O'REILLY, STEVEN STAMKOS",
 'zone': None,
 'coords_x': None,
 'coords_y': None,
 'danger': None,
 'high_danger': None,
 'player_1': None,
 'player_1_eh_id': None,
 'player_1_eh_id_api': None,
 'player_1_api_id': None,
 'player_1_position': None,
 'player_1_type': None,
 'player_2': None,
 'player_2_eh_id': None,
 'player_2_eh_id_api': None,
 'player_2_api_id': None,
 'player_2_position': None,
 'player_2_type': None,
 'player_3': None,
 'player_3_eh_id': None,
 'player_3_eh_id_api': None,
 'player_3_api_id': None,
 'player_3_position': None,
 'player_3_type': None,
 'score_state': '3v4',
 'score_diff': -1,
 '

{'id': 20240200170811,
 'season': 20242025,
 'session': 'R',
 'game_id': 2024020017,
 'game_date': '2024-10-10',
 'event_idx': 811,
 'period': 3,
 'period_seconds': 1200,
 'game_seconds': 3600,
 'strength_state': 'EvE',
 'event_team': 'DAL',
 'opp_team': 'NSH',
 'event': 'CHANGE',
 'description': 'PLAYERS OFF: LOGAN STANKOVEN, SAM STEEL, ESA LINDELL, JAKE OETTINGER, ILYA LYUBUSHKIN, TYLER SEGUIN',
 'zone': None,
 'coords_x': None,
 'coords_y': None,
 'danger': None,
 'high_danger': None,
 'player_1': None,
 'player_1_eh_id': None,
 'player_1_eh_id_api': None,
 'player_1_api_id': None,
 'player_1_position': None,
 'player_1_type': None,
 'player_2': None,
 'player_2_eh_id': None,
 'player_2_eh_id_api': None,
 'player_2_api_id': None,
 'player_2_position': None,
 'player_2_type': None,
 'player_3': None,
 'player_3_eh_id': None,
 'player_3_eh_id_api': None,
 'player_3_api_id': None,
 'player_3_position': None,
 'player_3_type': None,
 'score_state': '4v3',
 'score_diff': 1,
 'forwards_pe

{'id': 20240200170812,
 'season': 20242025,
 'session': 'R',
 'game_id': 2024020017,
 'game_date': '2024-10-10',
 'event_idx': 812,
 'period': 3,
 'period_seconds': 1200,
 'game_seconds': 3600,
 'strength_state': 'EvE',
 'event_team': 'NSH',
 'opp_team': 'DAL',
 'event': 'PEND',
 'description': 'PERIOD END- LOCAL TIME: 9:41 CDT',
 'zone': None,
 'coords_x': None,
 'coords_y': None,
 'danger': None,
 'high_danger': None,
 'player_1': None,
 'player_1_eh_id': None,
 'player_1_eh_id_api': None,
 'player_1_api_id': None,
 'player_1_position': None,
 'player_1_type': None,
 'player_2': None,
 'player_2_eh_id': None,
 'player_2_eh_id_api': None,
 'player_2_api_id': None,
 'player_2_position': None,
 'player_2_type': None,
 'player_3': None,
 'player_3_eh_id': None,
 'player_3_eh_id_api': None,
 'player_3_api_id': None,
 'player_3_position': None,
 'player_3_type': None,
 'score_state': '3v4',
 'score_diff': -1,
 'forwards_percent': 0.0,
 'opp_forwards_percent': 0.0,
 'shot_type': None,
 'eve

{'id': 20240200170813,
 'season': 20242025,
 'session': 'R',
 'game_id': 2024020017,
 'game_date': '2024-10-10',
 'event_idx': 813,
 'period': 3,
 'period_seconds': 1200,
 'game_seconds': 3600,
 'strength_state': 'EvE',
 'event_team': 'NSH',
 'opp_team': 'DAL',
 'event': 'GEND',
 'description': 'GAME END- LOCAL TIME: 9:41 CDT',
 'zone': None,
 'coords_x': None,
 'coords_y': None,
 'danger': None,
 'high_danger': None,
 'player_1': None,
 'player_1_eh_id': None,
 'player_1_eh_id_api': None,
 'player_1_api_id': None,
 'player_1_position': None,
 'player_1_type': None,
 'player_2': None,
 'player_2_eh_id': None,
 'player_2_eh_id_api': None,
 'player_2_api_id': None,
 'player_2_position': None,
 'player_2_type': None,
 'player_3': None,
 'player_3_eh_id': None,
 'player_3_eh_id_api': None,
 'player_3_api_id': None,
 'player_3_position': None,
 'player_3_type': None,
 'score_state': '3v4',
 'score_diff': -1,
 'forwards_percent': 0.0,
 'opp_forwards_percent': 0.0,
 'shot_type': None,
 'event

In [19]:
score_adjustments

strength_state  home_score_diff score_diff_group  home_goal_weight  \
0             5v5               -3         trailing          0.949278   
1             5v5               -2         trailing          0.949278   
2             5v5               -1         trailing          0.949278   
3             5v5                0             tied          0.959630   
4             5v5                1          leading          0.981420   
5             5v5                2          leading          0.981420   
6             5v5                3          leading          0.981420   
7             4v4               -3         trailing          0.939899   
8             4v4               -2         trailing          0.939899   
9             4v4               -1         trailing          0.939899   
10            4v4                0             tied          0.939899   
11            4v4                1          leading          0.939899   
12            4v4                2          leading          0.939899   
13            4v4                3          leading          0.939899   
14            3v3               -3              NaN          1.003687   
15            3v3               -2              NaN          1.003687   
16            3v3               -1              NaN          1.003687   
17            3v3                0              NaN          1.003687   
18            3v3                1              NaN          1.003687   
19            3v3                2              NaN          1.003687   
20            3v3                3              NaN          1.003687   
21            5v4               -3         trailing          0.868644   
22            5v4               -2         trailing          0.868644   
23            5v4               -1         trailing          0.868644   
24            5v4                0             tied          0.930994   
25            5v4                1          leading          0.994441   
26            5v4                2          leading          0.994441   
27            5v4                3          leading          0.994441   
28            5v3               -3         trailing          0.831858   
29            5v3               -2         trailing          0.831858   
30            5v3               -1         trailing          0.831858   
31            5v3                0             tied          0.943750   
32            5v3                1          leading          0.977273   
33            5v3                2          leading          0.977273   
34            5v3                3          leading          0.977273   
35            4v3               -3         trailing          0.837838   
36            4v3               -2         trailing          0.837838   
37            4v3               -1         trailing          0.837838   
38            4v3                0             tied          0.906566   
39            4v3                1          leading          0.807692   
40            4v3                2          leading          0.807692   
41            4v3                3          leading          0.807692   
42            1v0               -3         trailing          1.027778   
43            1v0               -2         trailing          1.027778   
44            1v0               -1         trailing          1.027778   
45            1v0                0             tied          0.989561   
46            1v0                1          leading          0.710526   
47            1v0                2          leading          0.710526   
48            1v0                3          leading          0.710526   

    away_goal_weight  home_pred_goal_weight  away_pred_goal_weight  \
0           1.056448               0.926516               1.086144   
1           1.056448               0.926516               1.086144   
2           1.056448               0.926516               1.086144   
3           1.043916               0.954719               1.049790   
4 

In [12]:
test_pickle

[{'strength_state': '5v5',
  'home_score_diff': -3,
  'score_diff_group': 'trailing',
  'home_goal_weight': 0.9492781520692974,
  'away_goal_weight': 1.0564481576692373,
  'home_pred_goal_weight': 0.9265162133062735,
  'away_pred_goal_weight': 1.0861441891318668,
  'home_shot_weight': 0.8776046468744237,
  'away_shot_weight': 1.1620681235502381,
  'home_fenwick_weight': 0.876901970566226,
  'away_fenwick_weight': 1.1633024487094639,
  'home_corsi_weight': 0.8595735290701726,
  'away_corsi_weight': 1.1952680878552973,
  'home_goal': 1603,
  'away_goal': 1431,
  'home_pred_goal': 1854.7022086515194,
  'away_pred_goal': 1522.5064434341027,
  'home_shot': 21692,
  'away_shot': 16382,
  'home_miss': 8777,
  'away_miss': 6363,
  'home_block': 10979,
  'away_block': 6784,
  'home_fenwick': 32072,
  'away_fenwick': 24176,
  'home_corsi': 43051,
  'away_corsi': 30960},
 {'strength_state': '5v5',
  'home_score_diff': -2,
  'score_diff_group': 'trailing',
  'home_goal_weight': 0.9492781520692974,

In [ ]:
score_adjustments = {}

for row in test_pickle:

    new_values = {row["strength_state"]: {}}

In [5]:
scraper = Scraper(2024020001)

In [8]:
stats = scraper.stats

In [9]:
stats

season session     game_id   game_date       player        eh_id  \
0    20242025       R  2024020001  2024-10-04    ALEX TUCH    ALEX.TUCH   
1    20242025       R  2024020001  2024-10-04    ALEX TUCH    ALEX.TUCH   
2    20242025       R  2024020001  2024-10-04    ALEX TUCH    ALEX.TUCH   
3    20242025       R  2024020001  2024-10-04    ALEX TUCH    ALEX.TUCH   
4    20242025       R  2024020001  2024-10-04    ALEX TUCH    ALEX.TUCH   
..        ...     ...         ...         ...          ...          ...   
139  20242025       R  2024020001  2024-10-04   TIMO MEIER   TIMO.MEIER   
140  20242025       R  2024020001  2024-10-04   TIMO MEIER   TIMO.MEIER   
141  20242025       R  2024020001  2024-10-04  TOMAS TATAR  TOMAS.TATAR   
142  20242025       R  2024020001  2024-10-04  TOMAS TATAR  TOMAS.TATAR   
143  20242025       R  2024020001  2024-10-04  TOMAS TATAR  TOMAS.TATAR   

      api_id position team opp_team strength_state        toi  g  ihdg  a1  \
0    8477949        R  BUF      NJD            4v5   1.766667  0     0   0   
1    8477949        R  BUF      NJD            5v4   3.466667  0     0   0   
2    8477949        R  BUF      NJD            5v5  17.000000  0     0   0   
3    8477949        R  BUF      NJD            5vE   0.216667  0     0   0   
4    8477949        R  BUF      NJD            Ev5   0.066667  0     0   0   
..       ...      ...  ...      ...            ...        ... ..   ...  ..   
139  8478414        R  NJD      BUF            5v5  15.266667  0     0   0   
140  8478414        R  NJD      BUF            Ev5   0.100000  0     0   0   
141  8475193        L  NJD      BUF            5v4   0.916667  0     0   0   
142  8475193        L  NJD      BUF            5v5  11.683333  0     0   0   
143  8475193        L  NJD      BUF            Ev5   0.366667  0     0   0   

     a2       ixg  isf  ihdsf  imsf  ihdm  iff  ihdf  isb  icf  ibs  igive  \
0     0  0.000000    0      0     0     0    0     0    0    0    0      0   
1     0  0.000000    0      0     0     0    0     0    2    2    0      0   
2     0  0.103262    2      1     0     0    2     1    1    3    1      2   
3     0  0.000000    0      0     0     0    0     0    0    0    0      0   
4     0  0.000000    0      0     0     0    0     0    0    0    0      0   
..   ..       ...  ...    ...   ...   ...  ...   ...  ...  ...  ...    ...   
139   0  0.158642    2      0     1     1    3     1    1    4    0      0   
140   0  0.000000    0      0     0     0    0     0    0    0    0      0   
141   0  0.000000    0      0     0     0    0     0    0    0    0      0   
142   0  0.000000    0      0     0     0    0     0    0    0    0      0   
143   0  0.000000    0      0     0     0    0     0    0    0    0      0   

     itake  ihf  iht  ifow  ifol  iozfw  iozfl  inzfw  inzfl  idzfw  idzfl  \
0        0    0    0     2     0      0      0      1      0      1      0   
1        0    0    0     1     4      1      0      0      0      0      4   
2        0    4    1     1     3      1      0      0      1      0      2   
3        0    0    0     0     0      0      0      0      0      0      0   
4        0    0    0     0     0      0      0      0      0      0      0   
..     ...  ...  ...   ...   ...    ...    ...    ...    ...    ...    ...   
139      0    5    0     1     0      0      0      1      0      0      0   
140      0    0    0     0     0      0      0      0      0      0      0   
141      0    0    0     0     0      0      0      0      0      0      0   
142      0    0    1     0     0      0      0      0      0      0      0   
143      0    0    0     0     0      0      0      0      0      0      0   

     a1_xg  a2_xg  ipent0  ipent2  ipent4  ipent5  ipent10  ipend0  ipend2  \
0      0.0    0.0       0       0       0       0        0       0       0   
1      0.0    0.0       0       0       0       0        0       0       0   
2      0.0    0.0       0       0       0       0        0   